<a href="https://colab.research.google.com/github/v-grand/Collector/blob/main/Crypto_ETL.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Instal

In [1]:
!pip install ta
!pip install mplfinance

  Preparing metadata (setup.py) ... done
  Created wheel for ta: filename=ta-0.11.0-py3-none-any.whl size=29412 sha256=a5e71bc31a0e3d17d47b0584585334531e005e61e59844abbf5a8c3f747cedad
  Stored in directory: /root/.cache/pip/wheels/a1/d7/29/7781cc5eb9a3659d032d7d15bdd0f49d07d2b24fec29f44bc4
Successfully built ta
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.0/75.0 kB 4.7 MB/s eta 0:00:00


### Import

In [3]:

'''
%pip install prophet

'''
import requests
import urllib

import pandas as pd

import matplotlib.pyplot as plt
import matplotlib.dates as mdates
import numpy as np

import pandas as pd
from prophet import Prophet

from datetime import datetime, timedelta
import numpy as np
from pandas import DataFrame
import pandas as pd


from sklearn.preprocessing import MinMaxScaler
import ta
from typing import Tuple
import yfinance as yf

from sklearn.ensemble import RandomForestRegressor
import pandas as pd
from sklearn.model_selection import train_test_split
import joblib
from sklearn.metrics import mean_squared_error


from google.colab import drive


# Function

In [ ]:
def scale_data(data:DataFrame, columns_x, columns_y) -> Tuple[MinMaxScaler, np.ndarray, np.ndarray]:

    # Prepare target variable
    y = data[columns_y].values
    X = data [columns_x]

    # Scale features
    scaler = MinMaxScaler(feature_range=(0, 1))
    X_scaled = scaler.fit_transform(X)
    y_scaled = scaler.fit_transform(y.reshape(-1, 1)).reshape(-1)

    return scaler, X_scaled, y_scaled

# EXTRACT

In [4]:
import yfinance as yf
import pandas as pd
import os

def extract_yf_data(ticker, periods, intervals):
    """
    Загружает данные для всех указанных интервалов и возвращает их в виде словаря.

    :param ticker: Символ тикера, например, 'BTC-USD'.
    :param periods: Период загрузки данных, например, '10y', 'max'.
    :param intervals: Список интервалов для загрузки данных, например, ['1m', '5m', '1d'].
    :return: Словарь с данными для каждого интервала.
    """
    datasets = {}

    for interval in intervals:
        try:
            print(f"Загрузка данных для интервала {interval}...")
            data = yf.download(tickers=ticker, period=periods, interval=interval)
            if data.empty:
                #print(f"Нет данных для интервала {interval}. Пропускаем.")
                continue
            else:
              # Добавляем столбец с интервалом для удобства
              #data['interval'] = interval

              # Сохраняем данные в словарь
              datasets[interval] = data
              print(f'{interval} ___ {datasets[interval].shape}')
              #print(datasets[interval].info())

        except Exception as e:
          pass
            #print(f"Ошибка при загрузке данных для интервала {interval}: {e}")

    print("Загрузка завершена.")
    return datasets




In [5]:
# Пример использования
ticker_ = 'BTC-USD'
period_ = 'max'
#intervals_ = ['1m', '2m', '5m', '15m', '30m', '60m', '90m', '1h', '1d', '5d', '1wk', '1mo', '3mo']
intervals_ = ['1m','5m', '15m', '30m', '60m', '90m', '1h', '1d', '5d', '1wk', '1mo', '3mo']



# Загрузка данных
extractdatasets = extract_yf_data (ticker_, period_, intervals_)

Загрузка данных для интервала 1m...


[*********************100%***********************]  1 of 1 completed


1m ___ (8067, 5)
Загрузка данных для интервала 5m...


[*********************100%***********************]  1 of 1 completed


5m ___ (17255, 5)
Загрузка данных для интервала 15m...


...

1h ___ (17436, 5)
Загрузка данных для интервала 1d...
1d ___ (3784, 5)
Загрузка данных для интервала 5d...


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


5d ___ (757, 5)
Загрузка данных для интервала 1wk...
1wk ___ (541, 5)
Загрузка данных для интервала 1mo...
1mo ___ (124, 5)
Загрузка данных для интервала 3mo...


[*********************100%***********************]  1 of 1 completed

3mo ___ (43, 5)
Загрузка завершена.


In [ ]:
for dataset in datasets:
  print(dataset)
print(datasets[dataset].head())

In [ ]:
print(datasets[dataset].head())

In [ ]:
print(datasets['1m'].info())

# TRANSFORM

In [ ]:
prepared_datasets = {}  # Словарь для хранения подготовленных данных

## Rename

In [ ]:
def process_dataframe(df, ticker_):
    # Сбрасываем индекс без добавления его в качестве нового столбца
    df.reset_index(inplace=True, drop=False)

    # Упрощаем MultiIndex, объединяя его уровни в строковые названия столбцов
    if isinstance(df.columns, pd.MultiIndex):
        df.columns = ['_'.join(filter(None, col)) if isinstance(col, tuple) else col for col in df.columns]

    # Попытка определить название временного столбца
    possible_time_columns = ['Datetime', 'Datet', 'index']  # Добавьте любые возможные варианты
    time_column = None
    for col in possible_time_columns:
        if col in df.columns:
            time_column = col
            df.rename(columns={time_column: 'D'}, inplace=True)

    if not time_column:
        raise ValueError("Не найден временной столбец ('Datetime', 'Date', или 'index') в данных.")

    # Переименовываем временной столбец в 'D'


    # Формируем словарь для переименования столбцов
    rename_dict = {
        f'Close_{ticker_}': 'C',
        f'High_{ticker_}': 'H',
        f'Low_{ticker_}': 'L',
        f'Open_{ticker_}': 'O',
        f'Volume_{ticker_}': 'V'
    }

    # Переименовываем столбцы
    df.rename(columns=rename_dict, inplace=True)

    return df


# Пример использования
prepared_datasets = {}  # Словарь для хранения обработанных наборов данных

for interval, dataset in datasets.items():
    print(f"Обработка {ticker_} данных для интервала {interval}...")

    try:
        prepared_data = process_dataframe(dataset, ticker_)
        prepared_datasets[interval] = prepared_data
    except ValueError as e:
        print(f"Ошибка при обработке интервала {interval}: {e}")


Обработка BTC-USD данных для интервала 1m...
Обработка BTC-USD данных для интервала 5m...
Обработка BTC-USD данных для интервала 15m...
Обработка BTC-USD данных для интервала 30m...
Обработка BTC-USD данных для интервала 60m...
Обработка BTC-USD данных для интервала 90m...
Обработка BTC-USD данных для интервала 1h...
Обработка BTC-USD данных для интервала 1d...
Обработка BTC-USD данных для интервала 5d...
Обработка BTC-USD данных для интервала 1wk...
Обработка BTC-USD данных для интервала 1mo...
Обработка BTC-USD данных для интервала 3mo...


In [ ]:
prepared_datasets['1m'].head()

D                         D              C              H              L  \
0  0 2025-01-17 14:36:00+00:00  102968.359375  102968.359375  102968.359375   
1  1 2025-01-17 14:39:00+00:00  102795.656250  102795.656250  102795.656250   
2  2 2025-01-17 14:40:00+00:00  102735.781250  102735.781250  102735.781250   
3  3 2025-01-17 14:41:00+00:00  102701.671875  102701.671875  102701.671875   
4  4 2025-01-17 14:42:00+00:00  102601.867188  102601.867188  102601.867188   

               O          V  
0  102968.359375          0  
1  102795.656250  330035200  
2  102735.781250   15425536  
3  102701.671875  217595904  
4  102601.867188   16183296

## Log_Close

In [ ]:
import numpy as np

def log_prices(df):
    """
    Логарифмирует столбец 'C' (цены закрытия) в переданном DataFrame.

    Аргументы:
    - df: pandas DataFrame, который должен содержать столбец 'C'.

    Возвращает:
    - DataFrame с добавленным столбцом 'Log_C', содержащим логарифм цен.
    """
    if 'C' not in df.columns:
        raise ValueError("Столбец 'C' (цены закрытия) отсутствует в данных.")

    # Добавляем логарифм цен в новый столбец 'Log_C'
    df['Log_C'] = np.log(df['C'])
    df['Log_O'] = np.log(df['O'])
    df['Log_H'] = np.log(df['H'])
    df['Log_L'] = np.log(df['L'])
    return df


# Пример использования:
for interval, dataset in prepared_datasets.items():
    print(f"Логарифмирование цен для интервала {interval}...")
    try:
        prepared_datasets[interval] = log_prices(dataset)
    except ValueError as e:
        print(f"Ошибка при обработке интервала {interval}: {e}")


Логарифмирование цен для интервала 1m...
Логарифмирование цен для интервала 5m...
Логарифмирование цен для интервала 15m...
Логарифмирование цен для интервала 30m...
Логарифмирование цен для интервала 60m...
Логарифмирование цен для интервала 90m...
Логарифмирование цен для интервала 1h...
Логарифмирование цен для интервала 1d...
Логарифмирование цен для интервала 5d...
Логарифмирование цен для интервала 1wk...
Логарифмирование цен для интервала 1mo...
Логарифмирование цен для интервала 3mo...


## calculate_ratios

In [ ]:
def calculate_ratios(df):
    """
    Добавляет в DataFrame отношения High, Low, Open к Close и Log_C.

    Аргументы:
    - df: pandas DataFrame, который должен содержать столбцы 'H', 'L', 'O', 'C', 'Log_C'.

    Возвращает:
    - DataFrame с добавленными столбцами отношений:
      - 'H_to_C', 'L_to_C', 'O_to_C' — отношения High, Low, Open к Close.
      - 'H_to_Log_C', 'L_to_Log_C', 'O_to_Log_C' — отношения High, Low, Open к Log_C.
    """
    required_columns = ['H', 'L', 'O', 'C', 'Log_C']
    missing_columns = [col for col in required_columns if col not in df.columns]

    if missing_columns:
        raise ValueError(f"Отсутствуют необходимые столбцы: {', '.join(missing_columns)}")

    # Расчет отношений к Close
    df['H_to_C'] = df['H'] / df['C']
    df['L_to_C'] = df['L'] / df['C']
    df['O_to_C'] = df['O'] / df['C']

    # Расчет отношений к Log_C
    df['H_to_Log_C'] = df['Log_H'] - df['Log_C']
    df['L_to_Log_C'] = -df['Log_L'] + df['Log_C']
    df['O_to_Log_C'] = df['Log_O'] - df['Log_C']

    return df


# Пример использования:
for interval, dataset in prepared_datasets.items():
    print(f"Вычисление отношений для интервала {interval}...")
    try:
        prepared_datasets[interval] = calculate_ratios(dataset)
    except ValueError as e:
        print(f"Ошибка при обработке интервала {interval}: {e}")


Вычисление отношений для интервала 1m...
Вычисление отношений для интервала 5m...
Вычисление отношений для интервала 15m...
Вычисление отношений для интервала 30m...
Вычисление отношений для интервала 60m...
Вычисление отношений для интервала 90m...
Вычисление отношений для интервала 1h...
Вычисление отношений для интервала 1d...
Вычисление отношений для интервала 5d...
Вычисление отношений для интервала 1wk...
Вычисление отношений для интервала 1mo...
Вычисление отношений для интервала 3mo...


In [ ]:
prepared_datasets['90m'].head()

D                   D             C             H             L  \
0  0 2024-11-25 13:30:00  95947.492188  97174.312500  95811.906250   
1  1 2024-11-25 15:00:00  96192.601562  96485.703125  94903.437500   
2  2 2024-11-25 16:30:00  95284.460938  96346.960938  94929.601562   
3  3 2024-11-25 18:00:00  94871.304688  95842.679688  94488.500000   
4  4 2024-11-25 19:30:00  94901.343750  95297.812500  94542.515625   

              O           V      Log_C      Log_O      Log_H      Log_L  \
0  97042.085938  1838112768  11.471556  11.482900  11.484262  11.470142   
1  95403.671875  6569713664  11.474108  11.465872  11.477150  11.460615   
2  96111.242188  2459262976  11.464622  11.473262  11.475711  11.460891   
3  95235.031250  4719906816  11.460277  11.464103  11.470463  11.456233   
4  95049.164062  4252311552  11.460593  11.462150  11.464762  11.456805   

     H_to_C    L_to_C    O_to_C  H_to_Log_C  L_to_Log_C  O_to_Log_C  
0  1.012786  0.998587  1.011408    0.012705    0.001414    0.011344  
1  1.003047  0.986598  0.991798    0.003042    0.013493   -0.008235  
2  1.011151  0.996276  1.008677    0.011089    0.003731    0.008640  
3  1.010239  0.995965  1.003834    0.010187    0.004043    0.003827  
4  1.004178  0.996219  1.001558    0.004169    0.003788    0.001556

In [ ]:
def prep_data(data, N_lag: int = 3, N_lead: int = 1, drop_na: bool = True) -> pd.DataFrame:
    """
    Подготавливает данные, добавляя сдвинутые значения для предсказаний.

    :param data: Исходный DataFrame, предварительно загруженный.
    :param N_lag: Количество шагов назад для создания признаков (сдвигов назад).
    :param N_lead: Количество шагов вперед для создания признаков (сдвигов вперед).
    :param drop_na: Удалять ли строки с NaN значениями.
    :return: Подготовленный DataFrame.
    """
    # Находим все столбцы, кроме временного столбца 'D'
    feature_columns = [col for col in data.columns if col != 'D']

    # Добавляем сдвиги назад
    for i in range(1, N_lag + 1):
        for col in feature_columns:
            data[f'{col}_lag{i}'] = data[col].shift(i)

    # Добавляем сдвиги вперед
    for i in range(1, N_lead + 1):
        for col in feature_columns:
            data[f'{col}_lead{i}'] = data[col].shift(-i)

    # Обрезаем строки, чтобы избежать NaN от сдвигов
    if drop_na:
        data.dropna(inplace=True)

    # Сбрасываем индекс после обработки
    data.reset_index(drop=True, inplace=True)

    # Вывод диапазона данных, если есть временной столбец
    if 'D' in data.columns:
        first_date_value = data['D'].iloc[0]
        last_date_value = data['D'].iloc[-1]
        print(f'Data loaded from {first_date_value} to {last_date_value}')

    return data


# Пример использования:
prepared_datasets = {}

# Пример цикла обработки
for interval, dataset in prepared_datasets.items():
    print(f"Подготовка данных для интервала {interval}...")
    try:
        # Задаем сдвиги назад и вперед
        prepared_datasets[interval] = prep_data(dataset, N_lag=5, N_lead=2)
    except Exception as e:
        print(f"Ошибка при обработке интервала {interval}: {e}")


## Shift

In [ ]:
# Словарь со значениями сдвигов назад (N_lag) и вперед (N_lead) для каждого интервала
shift_dict = {
    '1m': {'N_lag': 10, 'N_lead': 5},
    '5m': {'N_lag': 10, 'N_lead': 3},
    '15m': {'N_lag': 10, 'N_lead': 2},
    '30m': {'N_lag': 10, 'N_lead': 3},
    '60m': {'N_lag': 50, 'N_lead': 5},
    '90m': {'N_lag': 50, 'N_lead': 5},
    '1h': {'N_lag': 4, 'N_lead': 4},
    '1d': {'N_lag': 5, 'N_lead': 5},
    '5d': {'N_lag': 100, 'N_lead': 5},
    '1wk': {'N_lag': 160, 'N_lead': 4},
    '3mo': {'N_lag': 16, 'N_lead': 5}
}

prepared_datasets = {}  # Словарь для хранения подготовленных данных

# Обработка каждого интервала
for interval, dataset in datasets.items():
    print(f"Обработка данных для интервала {interval}...")
    shift_params = shift_dict.get(interval, {'N_lag': 3, 'N_lead': 5})  # Значения по умолчанию

    try:
        # Подготовка данных с учетом сдвигов назад и вперед
        prepared_data = prep_data(
            dataset,
            N_lag=shift_params['N_lag'],
            N_lead=shift_params['N_lead'],
            drop_na=True
        )
        prepared_datasets[interval] = prepared_data
    except Exception as e:
        print(f"Ошибка при обработке интервала {interval}: {e}")

print("Обработка данных завершена.")


Обработка данных для интервала 1m...


<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'{col}_lag{i}'] = data[col].shift(i)
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'{col}_lag{i}'] = data[col].shift(i)
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, u

Data loaded from D                           10
D    2025-01-17 14:50:00+00:00
Name: 0, dtype: object to D                         7800
D    2025-01-24 14:26:00+00:00
Name: 7790, dtype: object
Обработка данных для интервала 5m...


<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'{col}_lag{i}'] = data[col].shift(i)
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'{col}_lag{i}'] = data[col].shift(i)
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, u

Data loaded from D                           10
D    2024-11-25 15:25:00+00:00
Name: 0, dtype: object to D                        17253
D    2025-01-24 14:15:00+00:00
Name: 17243, dtype: object
Обработка данных для интервала 15m...
Data loaded from D                     10
D    2024-11-25 17:00:00
Name: 0, dtype: object to D                   5751
D    2025-01-24 14:00:00
Name: 5741, dtype: object
Обработка данных для интервала 30m...


...

Data loaded from 100 to 751
Обработка данных для интервала 1wk...


Выходные данные были обрезаны до нескольких последних строк (5000).
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'{col}_lag{i}'] = data[col].shift(i)
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'{col}_lag{i}'] = data[col].shift(i)
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at o

Data loaded from 160 to 536
Обработка данных для интервала 1mo...
Data loaded from 3 to 118
Обработка данных для интервала 3mo...


<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'{col}_lag{i}'] = data[col].shift(i)
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'{col}_lag{i}'] = data[col].shift(i)
<ipython-input-18-3f859ef3c7a1>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, u

Data loaded from 16 to 37
Обработка данных завершена.


In [ ]:
prepared_datasets['60m'].head()

D             C             H             L             O  \
0 2023-02-15 09:00:00  22160.253906  22160.253906  22112.865234  22119.224609   
1 2023-02-15 10:00:00  22249.544922  22250.605469  22161.140625  22174.589844   
2 2023-02-15 11:00:00  22451.498047  22469.326172  22235.986328  22247.783203   
3 2023-02-15 12:00:00  22763.789062  22816.482422  22451.300781  22451.300781   
4 2023-02-15 13:00:00  22727.263672  22770.298828  22715.724609  22765.140625   

            V      Log_C      Log_O      Log_H      Log_L  ...  Log_C_lead5  \
0           0  10.006056  10.004202  10.006056  10.003915  ...    10.029854   
1    61349888  10.010077  10.006702  10.010124  10.006096  ...    10.035617   
2  1021759488  10.019113  10.009998  10.019906  10.009467  ...    10.033695   
3  1953574912  10.032926  10.019104  10.035238  10.019104  ...    10.034674   
4           0  10.031321  10.032986  10.033212  10.030813  ...    10.041393   

   Log_O_lead5  Log_H_lead5  Log_L_lead5  H_to_C_lead5  L_to_C_lead5  \
0    10.031085    10.033369    10.028554      1.003521      0.998701   
1    10.030506    10.035818    10.030069      1.000201      0.994468   
2    10.035436    10.037659    10.033180      1.003972      0.999485   
3    10.033617    10.035149    10.033412      1.000476      0.998740   
4    10.034537    10.041393    10.033980      1.000000      0.992615   

   O_to_C_lead5  H_to_Log_C_lead5  L_to_Log_C_lead5  O_to_Log_C_lead5  
0      1.001232          0.003515          0.001300          0.001231  
1      0.994903          0.000201          0.005548         -0.005110  
2      1.001742          0.003964          0.000515          0.001741  
3      0.998944          0.000476          0.001261         -0.001057  
4      0.993168          0.000000          0.007413         -0.006855  

[5 rows x 7591 columns]

In [ ]:
#['1m','5m', '15m', '30m', '60m', '90m', '1h', '1d', '5d', '1wk', '1mo', '3mo']
# Пример использования с разными N_pred для каждого интервала
N_pred_dict = {
    '1m':1000,
    '5m':1000,
    '15m':1000,
    '30m':1000,
    '60m': 500,
    '90m': 500,
    '1h': 4,
    '1d': 2,
    '5d':100,
    '1wk':52,
    '3mo':16
}

prepared_datasets = {}  # Словарь для хранения подготовленных данных

for interval, dataset in datasets.items():
    print(f"Обработка данных для интервала {interval}...")
    N_pred = N_pred_dict.get(interval, 3)  # Получить N_pred для интервала, по умолчанию 3
    prepared_data = prep_data(dataset, N_pred=N_pred, drop_na=True, interval_=interval)
    prepared_datasets[interval] = prepared_data

Обработка данных для интервала 1m...


Выходные данные были обрезаны до нескольких последних строк (5000).
<ipython-input-76-8646dbca03db>:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevHigh_bar{i}'] = data['High'].shift(i)
<ipython-input-76-8646dbca03db>:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
<ipython-input-76-8646dbca03db>:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all co

   Data loaded from 2025-01-18 11:06:00+00:00 to 2025-01-24 10:23:00+00:00 interval 1m
Обработка данных для интервала 5m...


Выходные данные были обрезаны до нескольких последних строк (5000).
<ipython-input-76-8646dbca03db>:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
<ipython-input-76-8646dbca03db>:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevClose_bar{i}'] = data['Close'].shift(i)
<ipython-input-76-8646dbca03db>:17: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all 

   Data loaded from 2024-11-28 21:45:00+00:00 to 2025-01-24 10:20:00+00:00 interval 5m
Обработка данных для интервала 15m...


...

<ipython-input-76-8646dbca03db>:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevHigh_bar{i}'] = data['High'].shift(i)
<ipython-input-76-8646dbca03db>:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
<ipython-input-76-8646dbca03db>:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmente

   Data loaded from 2016-01-30 00:00:00 to 2025-01-17 00:00:00 interval 5d
Обработка данных для интервала 1wk...


<ipython-input-76-8646dbca03db>:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevHigh_bar{i}'] = data['High'].shift(i)
<ipython-input-76-8646dbca03db>:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  data[f'PrevLow_bar{i}'] = data['Low'].shift(i)
<ipython-input-76-8646dbca03db>:20: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmente

   Data loaded from 2015-09-14 00:00:00 to 2025-01-13 00:00:00 interval 1wk
Обработка данных для интервала 1mo...
   Data loaded from 2015-01-01 00:00:00 to 2024-12-01 00:00:00 interval 1mo
Обработка данных для интервала 3mo...
   Data loaded from 2018-09-01 00:00:00 to 2024-12-01 00:00:00 interval 3mo


<ipython-input-76-8646dbca03db>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.dropna(inplace=True)
<ipython-input-76-8646dbca03db>:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.rename(columns=lambda x: f'{x}_{interval_}', inplace=True)


##__

In [ ]:
prepared_datasets['1d'].head()

D       Date           C           H           L           O         V  \
0  5 2014-09-22  402.152008  406.915985  397.130005  399.100006  24127600   
1  6 2014-09-23  435.790985  441.557007  396.196991  402.092010  45099500   
2  7 2014-09-24  423.204987  436.112000  421.131989  435.751007  30627700   
3  8 2014-09-25  411.574005  423.519989  409.467987  423.156006  26814400   
4  9 2014-09-26  404.424988  414.937988  400.009003  411.428986  21460800   

      Log_C     Log_O     Log_H  ...  Log_C_lead5  Log_O_lead5  Log_H_lead5  \
0  5.996830  5.989212  6.008607  ...     5.990264     6.000315     6.007886   
1  6.077163  5.996681  6.090307  ...     5.932725     5.990141     5.994004   
2  6.047857  6.077071  6.077899  ...     5.928171     5.932054     5.953791   
3  6.019989  6.047741  6.048601  ...     5.958280     5.929823     5.968649   
4  6.002466  6.019636  6.028129  ...     5.949639     5.959527     5.969676   

   Log_L_lead5  H_to_C_lead5  L_to_C_lead5  O_to_C_lead5 H_to_Log_C_lead5  \
0     5.984873      1.017779      0.994624      1.010102         0.017623   
1     5.925143      1.063195      0.992447      1.059096         0.061279   
2     5.919539      1.025952      0.991405      1.003891         0.025621   
3     5.922765      1.010423      0.965109      0.971944         0.010369   
4     5.942222      1.020239      0.992610      1.009937         0.020037   

   L_to_Log_C_lead5  O_to_Log_C_lead5  
0          0.005391          0.010051  
1          0.007582          0.057416  
2          0.008632          0.003884  
3          0.035515         -0.028457  
4          0.007418          0.009888  

[5 rows x 177 columns]

In [ ]:
for dataset in prepared_datasets:
  print(dataset)
  print(prepared_datasets[dataset].info())

1m
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7778 entries, 0 to 7777
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype              
---  ------  --------------  -----              
 0   D       7778 non-null   int64              
 1   D       7778 non-null   datetime64[ns, UTC]
 2   C       7778 non-null   float64            
 3   H       7778 non-null   float64            
 4   L       7778 non-null   float64            
 5   O       7778 non-null   float64            
 6   V       7778 non-null   int64              
dtypes: datetime64[ns, UTC](1), float64(4), int64(2)
memory usage: 425.5 KB
None
5m
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17257 entries, 0 to 17256
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype              
---  ------  --------------  -----              
 0   D       17257 non-null  int64              
 1   D       17257 non-null  datetime64[ns, UTC]
 2   C       17257 non-null  float64            
 3   H       

In [ ]:
print(prepared_datasets[dataset].head())

   D       Date           C           H           L           O           V
0  0 2014-09-01  378.046997  457.092987  289.295990  387.427002  1562727810
1  1 2014-12-01  254.263000  384.037994  171.509995  378.248993  2363432922
2  2 2015-03-01  230.190002  300.044006  214.873993  254.283005  2199559600
3  3 2015-06-01  230.056000  314.394012  199.567001  230.233002  2534864700
4  4 2015-09-01  377.321014  495.562012  225.117004  230.255997  3734526796
